In [3]:
%load_ext autoreload
%autoreload 2

In [4]:
import os
import sys

root_dir = os.path.abspath(os.path.join(os.getcwd(), '../..'))
sys.path.insert(0, root_dir)

from custom_utils.config_handler import read_config, pprint_config

In [5]:
path_config = "../../conf/config.yaml"
global_cfg = read_config(path_config)
cfg = read_config(global_cfg.notebook_configs.finetune.finetune, root=global_cfg.root)
pprint_config(cfg)

{
  "mt_model": {
    "name": "transformer-en-ru",
    "model_and_tokenizer_name": "Helsinki-NLP/opus-mt-en-ru",
    "output_dir": "/Users/user010/Desktop/Programming/ML/En2RuTranslator/models/transformer-en-ru/finetuned"
  },
  "dataset": {
    "dir": "/Users/user010/Desktop/Programming/ML/En2RuTranslator/data/processed",
    "train": "/Users/user010/Desktop/Programming/ML/En2RuTranslator/data/processed/train.csv",
    "test": "/Users/user010/Desktop/Programming/ML/En2RuTranslator/data/processed/test.csv",
    "valid": "/Users/user010/Desktop/Programming/ML/En2RuTranslator/data/processed/valid.csv"
  },
  "finetune": {
    "batch_size": 16,
    "epochs": 3,
    "lr": 3e-05,
    "warmup_steps": 500,
    "weight_decay": 0.01,
    "grad_accum_steps": 3
  },
  "root": "/Users/user010/Desktop/Programming/ML/En2RuTranslator"
}


In [7]:
import transformers
print(transformers.__version__)

4.34.1


In [8]:
from datasets import load_dataset, load_metric
raw_datasets = load_dataset("waleko/unarXive-en2ru")
metric = load_metric("sacrebleu")

Extracting data files:   0%|          | 0/3 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

/var/folders/g1/r3wb2hk9311bvwjfb1lz48700000gp/T/ipykernel_45318/4136530936.py:3: FutureWarning: load_metric is deprecated and will be removed in the next major version of datasets. Use 'evaluate.load' instead, from the new library 🤗 Evaluate: https://huggingface.co/docs/evaluate
  metric = load_metric("sacrebleu")


In [9]:
raw_datasets

DatasetDict({
    train: Dataset({
        features: ['source', 'target'],
        num_rows: 9082
    })
    validation: Dataset({
        features: ['source', 'target'],
        num_rows: 702
    })
    test: Dataset({
        features: ['source', 'target'],
        num_rows: 568
    })
})

In [12]:
import numpy as np
n = 3
rnd_idx = np.random.randint(0, len(raw_datasets["train"]), n)
raw_datasets["train"][rnd_idx]

{'source': ['By\xa0[1]}, an \\(A\\) -covered variety \\(X\\)  is a geometric quotient of a very fllexible quasi-affine variety by an action of a torus. So the claim follows from Proposition\xa0Pr2.\n',
  'Example 5 Let \\(H\\)  be the brace of order 8 with additive group \\(\\mathbb {Z}_8\\)  having Socle of order 2 and \\((H,\\circ )=\\langle 1,2 \\rangle \\cong \\mathbb {Z}_4 \\times \\mathbb {Z}_2\\)  defined in [1]} and \\(I\\)  be brace of order 4 as defined in Example 3. Then we have total 8 different split semi-direct products of \\(I\\)  by \\(H\\) , interestingly with \\(\\mu _x=Id\\)  for all \\(x \\in H\\)  in all cases. We list few cases\n',
  'where the \\(\\sum \\)  means the summation of the resonances \\(\\rho , \\omega \\)  or \\(\\phi \\)  and their corresponding excited states, the\nexplicit expressions and auxiliary functions for BW and GS are referred to Refs.\xa0[1]}, [2]}. The parameters \\(c^K_{\\rho (\\omega ,\\phi )}\\)  have been fitted to the data in Refs\xa

In [13]:
metric

Metric(name: "sacrebleu", features: {'predictions': Value(dtype='string', id='sequence'), 'references': Sequence(feature=Value(dtype='string', id='sequence'), length=-1, id='references')}, usage: """
Produces BLEU scores along with its sufficient statistics
from a source against one or more references.

Args:
    predictions (`list` of `str`): list of translations to score. Each translation should be tokenized into a list of tokens.
    references (`list` of `list` of `str`): A list of lists of references. The contents of the first sub-list are the references for the first prediction, the contents of the second sub-list are for the second prediction, etc. Note that there must be the same number of references for each prediction (i.e. all sub-lists must be of the same length).
    smooth_method (`str`): The smoothing method to use, defaults to `'exp'`. Possible values are:
        - `'none'`: no smoothing
        - `'floor'`: increment zero counts
        - `'add-k'`: increment num/deno

In [14]:
fake_preds = ["hello there", "general kenobi"]
fake_labels = [["hello there"], ["general kenobi"]]
metric.compute(predictions=fake_preds, references=fake_labels)

{'score': 0.0,
 'counts': [4, 2, 0, 0],
 'totals': [4, 2, 0, 0],
 'precisions': [100.0, 100.0, 0.0, 0.0],
 'bp': 1.0,
 'sys_len': 4,
 'ref_len': 4}

In [15]:
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained(cfg.mt_model.model_and_tokenizer_name)
model = AutoModelForSeq2SeqLM.from_pretrained(cfg.mt_model.model_and_tokenizer_name)

/Users/user010/Desktop/Programming/ML/En2RuTranslator/venv/lib/python3.11/site-packages/transformers/models/marian/tokenization_marian.py:197: UserWarning: Recommended: pip install sacremoses.
  warnings.warn("Recommended: pip install sacremoses.")


The reason for such tokenization difference (as I think) is that actually for ru, and for en are used different tokenizers

In [16]:
example_sample = ["Привет, мир!"]
tokens_usual = tokenizer(example_sample)
with tokenizer.as_target_tokenizer():
    tokens_target = tokenizer(example_sample)

print("Tokens usual:", tokens_usual)
print("Tokens target:", tokens_target)

Tokens usual: {'input_ids': [[21, 2408, 779, 53, 222, 30, 275, 2, 21, 46, 53, 779, 56, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1]]}
Tokens target: {'input_ids': [[543, 1877, 2, 1920, 56, 0]], 'attention_mask': [[1, 1, 1, 1, 1, 1]]}


/Users/user010/Desktop/Programming/ML/En2RuTranslator/venv/lib/python3.11/site-packages/transformers/tokenization_utils_base.py:3848: UserWarning: `as_target_tokenizer` is deprecated and will be removed in v5 of Transformers. You can tokenize your labels by using the argument `text_target` of the regular `__call__` method (either in the same call as your input texts if you use the same keyword arguments, or in a separate call.
  warnings.warn(


In [29]:
max_length = 512

def preprocess_function(examples):
    inputs = [ex for ex in examples["source"]]
    targets = [ex for ex in examples["target"]]
    model_inputs = tokenizer(inputs, text_target=targets, max_length=max_length, truncation=True)
    return model_inputs

In [31]:
preprocess_function(raw_datasets['train'][:2])

{'source': ['We study the effectiveness of our proposed SAViR-T for solving the challenging RPM questions, specifically focusing on PGM\xa0[1]}, RAVEN\xa0[2]}, I-RAVEN\xa0[3]}, RAVEN-FAIR\xa0[4]}, and V-PROM\xa0[5]}. Details about the datasets can be found in the Supplementary. Next, we describe the experimental details of our simulations, followed by the results of these experiments and the performance analysis of obtained results, including an ablation study of our SAViR-T.\n', 'By comparing coefficients for \\(u^{r-l}\\)  in (REF ), we obtain the Pieri type formulas for the interpolation Jack polynomials, which are a higher order analogue of equation\xa0(5.3) in [1]} or equation\xa0(14.2) in\xa0[2]}.\n'], 'target': ['Мы изучаем эффективность нашего предложенного SAViR-T для решения сложных вопросов RPM, в основном сосредотачиваясь на PGM [1], RAVEN [2], I-RAVEN [3], RAVEN-FAIR [4] и V-PROM [5]. Подробности о наборах данных можно найти в Дополнительных материалах. Затем мы описываем 

{'input_ids': [[156, 1747, 4, 2877, 5, 338, 791, 289, 35659, 592, 2168, 11, 1491, 20, 26007, 4, 18426, 21, 58925, 1728, 2, 4657, 8220, 25, 542, 42118, 35409, 237, 12281, 2, 1113, 37966, 2293, 43511, 237, 12281, 2, 29, 11, 17992, 2637, 6786, 49308, 237, 12281, 2, 1113, 37966, 2293, 11, 2088, 9318, 202, 1565, 237, 12281, 2, 8, 1220, 11, 1291, 27328, 50881, 237, 12281, 3, 30276, 188, 4, 57893, 127, 36, 1179, 10, 4, 23571, 3, 13988, 2, 105, 12905, 4, 29850, 5812, 5, 338, 34254, 23, 2, 3758, 39, 4, 1133, 5, 310, 31483, 8, 4, 1717, 1880, 5, 5630, 1133, 2, 201, 77, 13, 32154, 1969, 1747, 5, 338, 289, 35659, 592, 2168, 11, 1491, 3, 0], [2470, 35588, 118, 29050, 23, 20, 21, 16779, 1145, 91, 57655, 39634, 1114, 11, 166, 12281, 16779, 24, 10, 14, 7825, 2088, 21, 117, 105, 5719, 4, 542, 9665, 592, 2526, 14236, 23, 20, 4, 1221, 17240, 1969, 8416, 16681, 3876, 104, 5967, 23, 2, 81, 55, 13, 2506, 427, 58437, 5, 27170, 14, 47763, 24, 10, 35409, 237, 12281, 64, 27170, 17408, 10073, 10, 43511, 237, 1228

In [32]:
tokenized_datasets = raw_datasets.map(preprocess_function, batched=True, remove_columns=["source", "target"])

Map:   0%|          | 0/9082 [00:00<?, ? examples/s]

{'source': ['We study the effectiveness of our proposed SAViR-T for solving the challenging RPM questions, specifically focusing on PGM\xa0[1]}, RAVEN\xa0[2]}, I-RAVEN\xa0[3]}, RAVEN-FAIR\xa0[4]}, and V-PROM\xa0[5]}. Details about the datasets can be found in the Supplementary. Next, we describe the experimental details of our simulations, followed by the results of these experiments and the performance analysis of obtained results, including an ablation study of our SAViR-T.\n', 'By comparing coefficients for \\(u^{r-l}\\)  in (REF ), we obtain the Pieri type formulas for the interpolation Jack polynomials, which are a higher order analogue of equation\xa0(5.3) in [1]} or equation\xa0(14.2) in\xa0[2]}.\n', 'Since the ground truth model parameters are known, the Mean Square Error (MSE) of the estimation is measured based on (see e.g., [1]}):\n\\( {\\rm MSE} = (\\hat{\\alpha } - \\alpha )^T\\frac{{\\bf X}^T_t{\\bf X}_t}{n}(\\hat{\\alpha } - \\alpha ),\\) \n', 'Theorem 1 (Variational con

Map:   0%|          | 0/702 [00:00<?, ? examples/s]

{'source': ['Definition 2 (Exponential Mechanism [1]}) \nLet \\(L_X: \\mathcal {X}^n \\times \\mathcal {Y} \\mapsto [0, \\infty ]\\)  be a measurable loss function for each \\(X \\in \\mathcal {X}^n\\) . Suppose, for all adjacent \\(X, X^{\\prime } \\in \\mathcal {X}^n\\)  and \\(y \\in \\mathcal {Y}\\) :\n\\(|L_X(y) - L_{X^{\\prime }}(y)| \\le \\Delta _L < \\infty .\\) \n', 'It is well-known that two-weight linear codes have better applications in secret sharing schemes [1]}, [2]}, association schemes [3]}, authentication codes [4]}, and so on. In particular, projective two-weight codes are very precious as they are closely related to finite projective spaces, strongly regular graphs and combinatorial\ndesigns [5]}, [6]}, [7]}. Here, we present the following two applications.\n', 'The non-commutative group Fourier transform, firstly introduced in [1]} for the Lie group \\(\\mathrm {SO}(3)\\) , is a natural choice of mapping between the configuration space and the corresponding momentu

Map:   0%|          | 0/568 [00:00<?, ? examples/s]

{'source': ['Reported methods for predicting the human blockage in mmWave communications include the use of 1) vision/camera[1]}, [2]}, [3]}, 2) radar[4]},\n3) LiDAR[5]}, and 4) sub-6 GHz channel[6]}, [7]}.\nHowever, those methods require and rely on an additional system to predict the moving blockage, thus adding cost and complexity to the implementation.\n', 'Definition 1 ([1]}, Definition 3.1.1) \nLet \\(E\\)  be a vector space over \\(\\mathbb {K}\\) . A function \\(p(\\cdot ):E\\rightarrow \\mathbb {R}_{+}\\)  is called an ultrametric seminorm if:\n', 'Yeast. Protein-to-protein interaction network in budding yeast, analyzed by [1]}. The network has \\(N = 1458\\)  vertices and \\(M = 1948\\)  edges.\n', '1. We model multilingual acronym extraction as a sequence labelling task and employed contextualized multilingual XLM-RoBERTa embeddings [1]}. Our system consists of a single model for multilingual acronym extraction and hence is practical for real-world usage.\n', "Compared to di

## Finetuning

In [33]:
from transformers import AutoModelForSeq2SeqLM, DataCollatorForSeq2Seq, Seq2SeqTrainingArguments, Seq2SeqTrainer

In [34]:
model = AutoModelForSeq2SeqLM.from_pretrained(cfg.mt_model.model_and_tokenizer_name)

In [35]:
batch_size = 16
model_name = cfg.mt_model.name
args = Seq2SeqTrainingArguments(
    model_name,
    evaluation_strategy = "epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=batch_size,
    per_device_eval_batch_size=batch_size,
    weight_decay=0.01,
    save_total_limit=3,
    num_train_epochs=1,
    predict_with_generate=True    
)

In [36]:
data_collator = DataCollatorForSeq2Seq(tokenizer, model=model)

In [37]:
import numpy as np
def postprocess_text(preds, labels):
    preds = [pred.strip() for pred in preds]
    labels = [[label.strip()] for label in labels]
    return preds, labels

def compute_metrics(eval_preds):
    preds, labels = eval_preds
    if isinstance(preds, tuple):
        preds = preds[0]
    decoded_preds = tokenizer.batch_decode(preds, skip_special_tokens=True)
    # The labels value for the text that is not being predicted gets set to -100. 
    # Replace these values with pad
    labels = np.where(labels != -100, labels, tokenizer.pad_token_id)
    decoded_labels = tokenizer.batch_decode(labels, skip_special_tokens=True)
    # Some simple post-processing
    decoded_preds, decoded_labels = postprocess_text(decoded_preds, decoded_labels)
    result = metric.compute(predictions=decoded_preds, references=decoded_labels)
    result = {"bleu": result["score"]}
    prediction_lens = [np.count_nonzero(pred != tokenizer.pad_token_id) for pred in preds]
    result["gen_len"] = np.mean(prediction_lens)
    result = {k: round(v, 4) for k, v in result.items()}
    return result

In [38]:
trainer = Seq2SeqTrainer(
    model,
    args,
    train_dataset=tokenized_datasets["train"],
    eval_dataset=tokenized_datasets["validation"],
    data_collator=data_collator,
    tokenizer=tokenizer,
    compute_metrics=compute_metrics
)

In [39]:
trainer.train()

  0%|          | 0/568 [00:00<?, ?it/s]

KeyboardInterrupt: 

In [ ]:
from transformers import MarianMTModel, MarianTokenizer

tokenizer = MarianTokenizer.from_pretrained(model_name)
model = MarianMTModel.from_pretrained(model_name)

In [ ]:
src_text = ['My name is Sarah and I live in London']
tokenized_text = tokenizer(src_text, return_tensors="pt", padding=True)
translated = model.generate(**tokenized_text)
decoded = tokenizer.batch_decode(translated, skip_special_tokens=True)

In [ ]:
for src, tran in zip(src_text, decoded):
    print(src, "-->", tran)